# Tutorial 10 – Linear Models

In this tutorial we will take a look at linear models both for regression and classification.

In [ ]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns

sns.set()  # make plots nicer

## Linear Regression

The basic idea of linear models is to make linear combinations of feature values and use them for prediction. In case of the linear regression the combination is directly the prediction. Formally,

$$ y = X \cdot w = 1w_0 + x_1w_1 + x_2w_2 + x_3w_3 \ldots + x_nw_n$$

where $X$ are input feature vectors, $w$ are coefficients learned by the model and $y$ are targets. $w_0$ is called intercept and it shifts the predictions so that the targets does not have to be normalized.

Let's take a look at linear regression in practice. We have a data about CO2 concentrations over the hundreds of years. Let's see if how well the linear model will fit this data.

In [ ]:
co2 = pd.read_csv("https://www.fi.muni.cz/ib031/datasets/CO2.csv")
co2.head()

In [ ]:
sns.lineplot(data=co2, x="Year", y="CO2")

In [ ]:
co2_X, co2_y = co2.drop(columns="CO2"), co2.CO2

Now we explore the possibilities of linear models. It is not necessary to split the dataset now. The goal is to observe how well the model can fit the training data.

<div class="alert alert-block alert-warning"><h5><b>Exercise 1</b></h5></div>

Use [LinearRegression](https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.LinearRegression.html) model to fit the data. Predict the CO2 level using the model and **\*save the predictions\*** into a variable called `predicted_co2`. Evaluate the model using **\*RMSE\***

You should get RMSE of $10.14$.

In [ ]:
# TODO: your code goes here...
# predicted_co2 = your code goes here...

---

We can visualize the fit by plotting predicted vales for each year.

In [ ]:
ax = sns.lineplot(data=co2, x="Year", y="CO2")
sns.lineplot(x=co2.Year, y=predicted_co2, ax=ax)

Clearly, this model does not have enough variance and it is unable to capture more steep increase of CO2 in the recent decades. Ideally, we would like to fit polynomials of higher degree. Luckily, linear models can do just that.

Although linear models will always create a linear combinations of features we can manipulate the features and create new ones to navigate around this limitation. We can introduce a new feature that is a second power of the original `year` feature.

In [ ]:
co2["year^2"] = co2.Year ** 2
co2_X = co2.drop(columns="CO2")

<div class="alert alert-block alert-warning"><h5><b>Exercise 2</b></h5></div>

Run the same code from Exercise 1 but this time save the prediction into a variable `predicted_co2_2`.

You should get RMSE of $5.64$.

In [ ]:
# TODO: your code goes here...
# predicted_co2_2 = your code goes here...

---

In [ ]:
ax = sns.lineplot(data=co2, x="Year", y="CO2")
sns.lineplot(x=co2.Year, y=predicted_co2, ax=ax)
sns.lineplot(x=co2.Year, y=predicted_co2_2, ax=ax)

The new model has half the RMSE of previous model and the predictions are visibly closer to the actual CO2 values. Using polynomials created from features is a common practice with linear models and there is even a transformer in `scikit-learn` just for this.

In [ ]:
if "year^2" in co2.columns:
    co2 = co2.drop(columns="year^2")

<div class="alert alert-block alert-warning"><h5><b>Exercise 3</b></h5></div>

Use [PolynomialFeatures](https://scikit-learn.org/stable/modules/generated/sklearn.preprocessing.PolynomialFeatures.html) to generate degree-4 polynomial features. Then fit the linear regression just like in previous exercises and save the prediction into a variable `predicted_co2_3`.

You should get RMSE of $1.38$.

In [ ]:
# TODO: your code goes here...
# predicted_co2_3 = your code goes here...

---

In [ ]:
ax = sns.lineplot(data=co2, x="Year", y="CO2")
sns.lineplot(x=co2.Year, y=predicted_co2, ax=ax)
sns.lineplot(x=co2.Year, y=predicted_co2_2, ax=ax)
sns.lineplot(x=co2.Year, y=predicted_co2_3, ax=ax)

The last model produces much closer fit. We could increase the polynomials' degree for better fit but that could result in overfitting. There are statistical tests (t-test) and methods to test when the model is too complex (ANOVA) but those are out of the scope of this tutorial. You can read more about ANOVA and how to use it in python in the [documentation of statsmodels](https://www.statsmodels.org/stable/examples/notebooks/generated/interactions_anova.html) package

Now let's generalize to multiple features. We have a dataset about cars and our goal is to predict how much miles per gallon a car can make based on the rest of the car's features.

In [ ]:
cars = sns.load_dataset("mpg")
display(cars.head())
cars.info()

Columns `origin` and `name` are impractical to use in linear model so we ignore them. 

In [ ]:
cars_X, cars_y = (
    cars[
        [
            "cylinders",
            "displacement",
            "horsepower",
            "weight",
            "acceleration",
            "model_year",
        ]
    ],
    cars.mpg,
)

In [ ]:
from sklearn.model_selection import train_test_split

cars_train_X, cars_test_X, cars_train_y, cars_test_y = train_test_split(
    cars_X, cars_y, test_size=0.2, random_state=42
)

<div class="alert alert-block alert-warning"><h5><b>Exercise 4</b></h5></div>

Use the [LinearRegression](https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.LinearRegression.html) model to predict the miles per gallon values of different cars. Save the predictions into a variable `cars_test_predicted` and evaluate the model using **\*RMSE\*** on test set. **\*Impute\*** any missing data.

You should get RMSE around $3.07$.

In [ ]:
# TODO: your code goes here...

---

Although we cannot easily visualize the hyperplane in six dimensions we can visualize the predictions and actual targets.

In [ ]:
def plot_scatter(true_y, predicted_y):
    min_value = min(true_y.min(), predicted_y.min())
    max_value = max(true_y.max(), predicted_y.max())

    plt.plot(
        [min_value, max_value],
        [min_value, max_value],
        c="black",
    )
    plt.xlabel("predictions")
    sns.scatterplot(x=predicted_y, y=true_y)


plot_scatter(cars_test_y, cars_test_predicted)

Ideally, all the points should be on the black line. Then our predictions would be perfect. This is not the case and there is a slight upward "curve" in the data. Therefore, we might improve the model using polynomial features.

<div class="alert alert-block alert-warning"><h5><b>Exercise 5</b></h5></div>

Extend the model from Exercise 4 with [PolynomialFeatures](https://scikit-learn.org/stable/modules/generated/sklearn.preprocessing.PolynomialFeatures.html) transformer generating degree-4 polynomials. Evaluate the model using **\*RMSE\*** on test set and visualize the result using **\*scatter plot\***.

You should get RMSE of $32.0$.

In [ ]:
# TODO: your code goes here...

---

The RMSE is much worse mainly due to the single outlier. This, however, illustrates that outlying values are amplified in polynomials as higher powers of extreme values become even more extreme. We now have two possibilities:
1. remove the outlier, or
2. select only a subset of polynomial features.

Let's go with option 2.

<div class="alert alert-block alert-warning"><h5><b>Exercise 6</b></h5></div>

Extend the model from Exercise 5 with feature selection that will keep only **\*40 best\*** performing features. Evaluate the model using **\*RMSE\*** on test set and visualize the result using **\*scatter plot\***.

You should get RMSE of $2.55$.

In [ ]:
# TODO: your code goes here...

---

The points now have a straight trend and they are closer to the ideal black line. RMSE has also improved.

Instead of explicitly selecting features we can use a modification of linear regression called Lasso. Lasso adds L1 regularization to coefficients ($w_i$) that forces them to be small and zero if possible. This acts as feature selection where only non-zero coefficients mark "selected" features.

<div class="alert alert-block alert-warning"><h5><b>Exercise 7</b></h5></div>

Extend and modify the model from Exercise 5 to use [Lasso](https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.Lasso.html) instead of `LinearRegression` and **\*standardize\*** the polynomial features. Evaluate the model using **\*RMSE\*** on test set and visualize the result using **\*scatter plot\***. Find out which features have non-zero coefficients.

You should get RMSE of $2.87$.

In [ ]:
# TODO: your code goes here...

---

The RMSE is a bit worse but Lasso is using only 5 features instead of 40.

## Robust Regression

Basic linear regression is fairly sensitive to outliers. This is due to the fact that it optimizes sum of square errors. Square errors of outliers are particularly big and the model tries to compensate for it. Luckily, there are more robust versions of linear regression that are not that sensitive to outliers.

We explore this weakness on the following synthetic dataset.

In [ ]:
np.random.seed(42)
X = np.arange(100)
y = X + np.random.normal(0, 5, 100)
y[0] = 100
y[99] = 0
sns.scatterplot(x=X, y=y)

In [ ]:
from sklearn.linear_model import TheilSenRegressor

lr = LinearRegression()
lr.fit(X.reshape(-1, 1), y)

ts = TheilSenRegressor()
ts.fit(X.reshape(-1, 1), y)


plt.plot([0, 100], [0, 100], c="green")
plt.plot([0, 100], lr.predict([[0], [100]]), c="red")
plt.plot([0, 100], ts.predict([[0], [100]]), c="orange")
sns.scatterplot(x=X, y=y)

The green line is the ground truth that the model should ideally discover. The red line is basic linear regression and it is rotated in the direction of outliers. The orange line is Theil-Sen estimator that is one of the robust estimators. The orange line is much closer to the ground truth green line.

## Logistic regression

Despite its name, logistic regression is used for classification. It is still considered a (generalized) linear model as the main component is the linear combination of features that is then transformed using a logistic function. This results in the output in range [0, 1] that is interpreted as probability. Formally

$$ P(y=1) = \sigma(X \cdot w) = \frac{1}{1 + e^{-X \cdot w}} $$

where $X$ are input features, $w$ are coefficients, and $P(y=1)$ is probability that the class label for the given example is 1.

Let's try logistic regression for classifying diabetes.

In [ ]:
diabetes = pd.read_csv("https://www.fi.muni.cz/ib031/datasets/diabetes.csv")

diabetes.Glucose.replace(0, np.nan, inplace=True)
diabetes.BloodPressure.replace(0, np.nan, inplace=True)
diabetes.SkinThickness.replace(0, np.nan, inplace=True)
diabetes.Insulin.replace(0, np.nan, inplace=True)
diabetes.BMI.replace(0, np.nan, inplace=True)

diabetes.dropna(inplace=True)
diabetes.reset_index(drop=True, inplace=True)

diabetes.head()

In [ ]:
diabetes_X, diabetes_y = diabetes.drop(columns="Outcome"), diabetes.Outcome

diabetes_train_X, diabetes_test_X, diabetes_train_y, diabetes_test_y = train_test_split(
    diabetes_X, diabetes_y, test_size=0.2, random_state=42
)

<div class="alert alert-block alert-warning"><h5><b>Exercise 8</b></h5></div>

Use [LogisticRegression](https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.LogisticRegression.html) to classify Indians with diabetes. Evaluate the model using **\*accuracy\*** and compare the accuracy with a **\*baseline model\*** predicting the most frequent class.

You should get accuracy of $0.77$ that should be a bit better than baseline model.

In [ ]:
# TODO: your code goes here...

---